In [1]:
import numpy as np
import pandas as pd
import json
import matplotlib.pyplot as plt

import os
import matplotlib.pyplot as plt
import cv2


In [17]:
df = pd.read_csv('E:/collage/5TH Term/tools/project/full_df.csv')
raw_data = df.drop(columns=['N', 'D', 'G', 'C', 'A', 'H', 'M', 'O', 'labels'])

In [18]:
raw_data["target"]=raw_data["target"].apply(eval)
raw_data["target"][0]

[1, 0, 0, 0, 0, 0, 0, 0]

In [5]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms, models
from PIL import Image

In [19]:
img_dir = "E:/collage/5TH Term/tools/project/preprocessed_images/"
for i in range(len(raw_data)):
    raw_data["Left-Fundus"][i] = img_dir + raw_data["Left-Fundus"][i]
    raw_data["Right-Fundus"][i] = img_dir + raw_data["Right-Fundus"][i]

C:\Users\Fast\AppData\Local\Temp\ipykernel_16264\1627729451.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  raw_data["Left-Fundus"][i] = img_dir + raw_data["Left-Fundus"][i]
C:\Users\Fast\AppData\Local\Temp\ipykernel_16264\1627729451.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  raw_data["Right-Fundus"][i] = img_dir + raw_data["Right-Fundus"][i]
C:\Users\Fast\AppData\Local\Temp\ipykernel_16264\1627729451.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#re

In [20]:
for i in range(len(raw_data)):
    if(os.path.exists(raw_data["Left-Fundus"][i]) and os.path.exists(raw_data["Right-Fundus"][i])):
        continue
    else: raw_data =  raw_data.drop(i)

In [21]:
imgPathes = []
for i in range(len(raw_data)):
    imgPathes.append((raw_data["Left-Fundus"].values[i]))
    imgPathes.append((raw_data["Right-Fundus"].values[i]))

In [25]:
class OcularDataset(Dataset):
    def __init__(self, img_paths, target_labels, transform=None):
        self.img_paths = img_paths
        self.target_labels = target_labels
        self.transform = transform

    def __len__(self):
        return len(self.img_paths) // 2

    def __getitem__(self, idx):
        idx *= 2
        img_path_left = self.img_paths[idx]
        img_path_right = self.img_paths[idx + 1]

        image_left = Image.open(img_path_left).convert("RGB")
        image_right = Image.open(img_path_right).convert("RGB")

        if self.transform:
            image_left = self.transform(image_left)
            image_right = self.transform(image_right)

        # Concatenate along the channel dimension
        image = torch.cat([image_left, image_right], dim=0)

        label = self.target_labels[idx // 2]

        return image, label


target_labels = torch.Tensor(raw_data["target"])

transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

dataset = OcularDataset(imgPathes, target_labels, transform)

train_size = int(0.8 * len(dataset))
test_size = len(dataset) - train_size
train_dataset, test_dataset = torch.utils.data.random_split(dataset, [train_size, test_size])

train_loader = DataLoader(train_dataset, batch_size=64, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=64, shuffle=False)


In [29]:
len(train_loader)

76

In [30]:
class OcularModel(nn.Module):
    def __init__(self, num_classes):
        super(OcularModel, self).__init__()
        self.base_model = models.resnet50(pretrained=True)
        
        self.base_model.conv1 = nn.Conv2d(6, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
        
        self.fc = nn.Linear(1000, num_classes)

    def forward(self, x):
        x = self.base_model(x)
        x = self.fc(x)
        return x

model = OcularModel(8)

criterion = nn.BCEWithLogitsLoss()
optimizer = optim.Adam(model.parameters(), lr=0.001)

num_epochs = 4
for epoch in range(num_epochs):
    model.train()
    for images, labels in train_loader:
        optimizer.zero_grad()
        outputs = model(images)
        loss = criterion(outputs, labels)
        print(loss)
        loss.backward()
        optimizer.step()

    print(f"Epoch {epoch + 1}/{num_epochs}, Loss: {loss.item()}")


E:\Programs\anaconda\Lib\site-packages\torchvision\models\_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
E:\Programs\anaconda\Lib\site-packages\torchvision\models\_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


tensor(0.8117, grad_fn=<BinaryCrossEntropyWithLogitsBackward0>)
tensor(0.4538, grad_fn=<BinaryCrossEntropyWithLogitsBackward0>)
tensor(0.6386, grad_fn=<BinaryCrossEntropyWithLogitsBackward0>)
tensor(0.5282, grad_fn=<BinaryCrossEntropyWithLogitsBackward0>)
tensor(0.4690, grad_fn=<BinaryCrossEntropyWithLogitsBackward0>)
tensor(0.3692, grad_fn=<BinaryCrossEntropyWithLogitsBackward0>)
tensor(0.3462, grad_fn=<BinaryCrossEntropyWithLogitsBackward0>)
tensor(0.3470, grad_fn=<BinaryCrossEntropyWithLogitsBackward0>)
tensor(0.4018, grad_fn=<BinaryCrossEntropyWithLogitsBackward0>)
tensor(0.3306, grad_fn=<BinaryCrossEntropyWithLogitsBackward0>)
tensor(0.3204, grad_fn=<BinaryCrossEntropyWithLogitsBackward0>)
tensor(0.3424, grad_fn=<BinaryCrossEntropyWithLogitsBackward0>)
tensor(0.2887, grad_fn=<BinaryCrossEntropyWithLogitsBackward0>)
tensor(0.3103, grad_fn=<BinaryCrossEntropyWithLogitsBackward0>)
tensor(0.3116, grad_fn=<BinaryCrossEntropyWithLogitsBackward0>)
tensor(0.3331, grad_fn=<BinaryCrossEntro

In [34]:
len(test_loader)

19

In [50]:
model.eval()
with torch.no_grad():
    correct = 0
    total = 0
    for images, labels in test_loader:
        outputs = model(images)
        predicted = torch.round(torch.sigmoid(outputs))
        total += len(labels)
        for i in range(len(predicted)):
            comparison = torch.eq(predicted[i], labels[i])
            are_equal = torch.all(comparison).item()
            if(are_equal):
                correct+=1
            else: continue    
        print(correct/total)


    accuracy = correct / total
    print(f"Test Accuracy: {accuracy:.4f}")

torch.save(model.state_dict(), "E:/collage/5TH Term/tools/project/m.model")

0.265625
0.25
0.28125
0.28125
0.296875
0.3072916666666667
0.30357142857142855
0.306640625
0.3038194444444444
0.3109375
0.3096590909090909
0.3098958333333333
0.3076923076923077
0.3046875
0.3072916666666667
0.3017578125
0.30514705882352944
0.3098958333333333
0.30971993410214166
Test Accuracy: 0.3097
